In [83]:
import asyncio
import random
import logging
from logging import getLogger, StreamHandler, Formatter, FileHandler, DEBUG
import json
import math
import statistics
from datetime import datetime as dt
import os

logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

In [84]:
class Architecture():
    def __init__(self, config, D=3, G=2, C=2, transfer_rate=0.5, rec_max=100):
        self._name = config["name"]
        self._mod_dict = {}
        self._env_list = config["env_list"]
        self._goal_env = config["goal_env"]
        self._conflict_env = config["conflict_env"]
        self._pre_modules = {}
        self._next_modules = {}
        self._D = 10
        self._G = 6
        self._C = 2
        self._transfer_rate = transfer_rate
        self._rec_max = rec_max
        self._cnt = 0
        self._spread_mod = []
        self._activate_mod_cnt = 0
    
    @property
    def rec_cnt(self):
        return self._rec_cnt
    
    @property
    def module_dict(self):
        return self._mod_dict
    
    @property
    def env_list(self):
        return self._env_list
    
    @property
    def goal_env(self):
        return self._goal_env
    
    @property
    def pre_modules(self):
        return self._pre_modules
    
    @pre_modules.setter
    def pre_modules(self, pre_modules):
        self._pre_modules = pre_modules
    
    @property
    def next_modules(self):
        return self._next_modules
    
    @next_modules.setter
    def next_modules(self, next_modules):
        self._next_modules = next_modules
    
    def add_module(self, module_name, module):
        self._mod_dict[module_name] = module
        module.architecture = self
    
    def delete_module(self, module_name, module):
        self._mod_dict.pop(module_name)
        module.architecture = None
        
    def next_modules(self):
        next_modules = {}
        for name, mod in self._mod_dict.items():
            next_modules[name] = mod.next_module()
        return next_modules

    def pre_modules(self):
        pre_modules = {}
        for name, mod in self._mod_dict.items():
            pre_modules[name] = mod.pre_module()
        return pre_modules    
    
    def loop(self):
        while True:
            if (set(self._goal_env) & set(self._env_list)) == set(self._goal_env):
                break
            # distance伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._env_list) & set(mod._cnames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.forward_update(self._D, "")
            # goal伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._goal_env) & set(mod._anames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.backward_update(self._G, "")

            # conflict伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._conflict_env) & set(mod._dnames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.conflict_update(self._C, "")
                        
            if random.random() < 0.2:
                self._env_list = list(set(self._env_list) | set(["object observed"]))

In [110]:
class Module():
    def __init__(self, config):
        self._name = config["name"]
        self._mtype = config["module_type"]
        self._threshold = config["threshold"]
        self._intensity = config["intensity"]
        self._cnames = config["condition_list"]
        self._anames = config["add_list"]
        self._dnames = config["delete_list"]
        self._arc = None
        self._level = 0
        self._transfer_rate_mod = 1
        
    @property
    def module_type(self):
        return self._mtype
    
    @property
    def architecture(self):
        return self._arc
    
    @architecture.setter
    def architecture(self, architecture):
        self._arc = architecture
    
    def is_active(self):
        return self._level >= self._threshold and set(self._cnames) == (set(self._cnames) & set(self._arc._env_list))
    
    @property
    def transfer_success(self):
        return random.random() <= self._transfer_reliability
    
    def function(self):
        self._arc._activate_mod_cnt += 1
        print("{}. ======activate : {}=======".format(self._arc._activate_mod_cnt,self._name))
        self._arc._env_list = list(set(self._arc._env_list)|set(self._anames))
        self._arc._env_list = list(set(self._arc._env_list)-set(self._dnames))
        self._transfer_rate_mod *= 0.5
        self._level = 0
        self._active = False
    
    def next_module(self):
        """
        condition_listを通じてリンクしている次のモジュールを格納
        """
        next_module_list = []
        for _, mod in self._arc._mod_dict.items():
            for add in self._anames:
                if add in mod._cnames:
                    next_module_list.append(mod)
        return next_module_list
    
    def pre_module(self):
        """
        condition_listを通じてリンクしている前のモジュールを格納
        """
        pre_module_list = []
        for _, mod in self._arc._mod_dict.items():
            for condition in self._cnames:
                if condition in mod._anames:
                    pre_module_list.append(mod)
        return pre_module_list
    
    def forward_update(self, spread, pre_name):
        self._arc._spread_mod.append(self._name)
        self._arc._cnt += 1
        if self._arc._cnt > self._arc._rec_max:
            pass
        else:
            update_level = spread * self._arc._transfer_rate * self._transfer_rate_mod
            self._level += update_level
            if self.is_active():
                self.function()
            if len(self._arc.next_modules[self._name]) != 0:
                for mod in self._arc.next_modules[self._name]:
                    if mod._name != pre_name and mod._name not in self._arc._spread_mod:
                        mod.forward_update(update_level, self._name)
    
    def backward_update(self, spread, next_name):
        self._arc._spread_mod.append(self._name)
        self._arc._cnt += 1
        if self._arc._cnt > self._arc._rec_max:
            pass
        else:
            update_level = spread * self._arc._transfer_rate * self._transfer_rate_mod
            self._level += update_level
            if self.is_active():
                self.function()
            if len(self._arc.pre_modules[self._name]) != 0:
                for mod in self._arc.pre_modules[self._name]:
                    if mod._name != next_name and mod._name not in self._arc._spread_mod:
                        mod.backward_update(update_level, self._name)

    def conflict_update(self, spread, next_name):
        self._arc._spread_mod.append(self._name)
        self._arc._cnt += 1
        if self._arc._cnt > self._arc._rec_max:
            pass
        else:
            update_level = spread * self._arc._transfer_rate * self._transfer_rate_mod
            self._level -= update_level
            if self.is_active():
                self.function()
            if len(self._arc.pre_modules[self._name]) != 0:
                for mod in self._arc.pre_modules[self._name]:
                    if mod._name != next_name and mod._name not in self._arc._spread_mod:
                        mod.conflict_update(update_level, self._name)    

In [111]:
class AntArchitecture(Architecture):
    def __init__(self, config, spread_num):
        super().__init__(config)
        self._reward = 0
        self._spread_num = spread_num
    
    @property
    def thresholds(self):
        return [mod.threshold for mod in self.module_dict.values()]
    
    @thresholds.setter
    def thresholds(self, thresholds):
        for module, t in zip(self.module_dict.values(), thresholds):
            module.threshold = t

    @property
    def reward(self):
        return self._reward
    
    @reward.setter
    def reward(self, r):
        self._reward = r

    def loop(self):
        i = 0
        while True:
            i += 1
            if i > self._spread_num:
                self.reward = 0
                break
            if (set(self._goal_env) & set(self._env_list)) == set(self._goal_env):
                self.reward = 1/self._activate_mod_cnt
                break
            # distance伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._env_list) & set(mod._cnames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.forward_update(self._D, "")
            # goal伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._goal_env) & set(mod._anames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.backward_update(self._G, "")

            # conflict伝播
            self._cnt = 0
            self._spread_mod = []
            for name, mod in self._mod_dict.items():
                if len((set(self._conflict_env) & set(mod._dnames))) > 0:
                    if mod._name not in self._spread_mod:
                        mod.conflict_update(self._C, "")
                        
            if random.random() < 0.2:
                self._env_list = list(set(self._env_list) | set(["object observed"]))

In [112]:
class AntModule(Module):
    def __init__(self, config):
        super().__init__(config)
        
    @property
    def threshold(self):
        return self._threshold
    
    @threshold.setter
    def threshold(self, threshold):
        self._threshold = threshold
    
    @property
    def name(self):
        return self._name

In [117]:
class Train():
    def __init__(self, file_path, N=100, epochs=100, spread_num= 100, mutation_rate=0.05):
        self._file_path = file_path
        self._N = N
        self._epochs = epochs
        self._mutation_rate = mutation_rate
        self._architectures = []
        self._num_module = 0
        self._rewards = []
        self._architectures_that_get_reward = []
        self._spread_num = spread_num
        
    @property
    def architectures(self):
        return self._architectures
        
    @architectures.setter
    def architectures(self, update_architectures):
        self._architectures = update_architectures
        
    @property
    def architectures_that_get_reward(self):
        return self._architectures_that_get_reward
        
    @property
    def rewards(self):
        return self._rewards
        
    @rewards.setter
    def rewards(self, update_rewards):
        self._rewards = update_rewards
        
    @property
    def num_module(self):
        return self._num_module
        
    def set_data(self, init_architecture):
        with open("./config.json") as f:
            config = json.load(f)
            
        architecture_config = config["architecture_config"]
        module_configs = config["module_configs"]
            
        for i in range(self._N):
            architecture = AntArchitecture(architecture_config, spread_num=self._spread_num)
            for module_config in module_configs:
                module = AntModule(module_config)
                architecture.add_module(module_config["name"], module)
                
            architecture.next_modules = architecture.next_modules()
            architecture.pre_modules = architecture.pre_modules()
                
            init_architecture.append(architecture)
            
        self._num_module = len(init_architecture[0].module_dict)
            
        init_thresholds = [[random.randint(0, 100) for _ in range(self._num_module)] for _ in range(self._N)]
            
        for i in range(self._N):
            init_architecture[i].thresholds = init_thresholds[i]
        
    def train(self):
        for epoch in range(self._epochs):
            print("============{} epochs============".format(epoch+1))
            self.calc_reward()
            self.sort_architecture()
            if epoch != self._epochs-1:
                self.uniform_cross()
        
    def calc_reward(self):
        self.rewards = []# 報酬値のリスト
        for i in range(self._N):
            print(self.architectures[i]._env_list)
            self.architectures[i].loop()
            self.rewards.append(self.architectures[i].reward)
        print("Goal状態が達成されたアーキテクチャの数: {}".format(self._N - self.rewards.count(0)))
        
    def sort_architecture(self):
        architectures_reward = dict(zip(self.architectures, self.rewards))
        architectures_reward_list = sorted(architectures_reward.items(), key=lambda x: x[1], reverse=True)
        architectures_reward.clear()
        architectures_reward.update(architectures_reward_list)
        self.rewards = list(architectures_reward.values())
        self.architectures = list(architectures_reward.keys())
        # デバック用のプリント
        print("reward: {}".format(self.rewards[:5]))
        print("平均: {:.2f}, 分散: {:.2f}".format(statistics.mean(self.rewards), statistics.pstdev(self.rewards)))            
        
    def uniform_cross(self):
        next_architectures = []    # 子供世代のアーキテクチャ集合
        self.set_data(next_architectures)

        # 子供世代の作成
        for i in range(self._N):
            # 子個体のパラメータのリスト
            next_architecture_thresholds = []
            # 親の選択
            parents_architectures = random.choices(self.architectures, k=2, weights=self.rewards)
            # 親のパラメータの保存
            parents_architecture_thresholds = []
            parents_architecture_thresholds.append(parents_architectures[0].thresholds)
            parents_architecture_thresholds.append(parents_architectures[1].thresholds)

            for mod_num in range(self._num_module):
                ## 閾値の更新
                # 突然変異
                if random.random() < self._mutation_rate:
                    next_architecture_thresholds.append(random.randint(1, 100))
                # 突然変異でなければ、一様交叉
                else:
                    if random.random() < 0.5:
                        next_architecture_thresholds.append(parents_architecture_thresholds[0][mod_num])
                    else:
                        next_architecture_thresholds.append(parents_architecture_thresholds[1][mod_num])

            next_architectures[i].thresholds = next_architecture_thresholds

        self.architectures = next_architectures

In [118]:
# def main():
#     with open("./config.json") as f:
#         config = json.load(f)
#     architecture_config = config["architecture_config"]
#     module_configs = config["module_configs"]
    
#     architecture = Architecture(architecture_config)
    
#     for module_config in module_configs:
#         module = Module(module_config)
#         architecture.add_module(module_config["name"], module)
        
#     architecture.next_modules = architecture.next_modules()
#     architecture.pre_modules = architecture.pre_modules()
    
#     architecture.loop()

In [119]:
def main():
    file_path = "./config.json"
    # trainインスタンスの作成
    train = Train(file_path=file_path)
    # データのセット
    train.set_data(init_architecture=train.architectures)
    # 訓練
    train.train()
    
    # 訓練で得られたアーキテクチャの取得
    train_architectures = train.architectures
    
    # テスト用にモジュール名とモジュールの活性値を出力
    for i in range(1):
        for mod_name, mod_class in train_architectures[i].module_dict.items():
            print("{} 閾値: {}".format(mod_name, mod_class.threshold))
    
    # 伝播してみる
    architecture_thresholds = train_architectures[0].thresholds
    
    with open("./config.json") as f:
        config = json.load(f)
    architecture_config = config["architecture_config"]
    module_configs = config["module_configs"]
    
    architecture = AntArchitecture(architecture_config, spread_num=50)
    
    for module_config in module_configs:
        module = AntModule(module_config)
        architecture.add_module(module_config["name"], module)
        
    architecture.next_modules = architecture.next_modules()
    architecture.pre_modules = architecture.pre_modules()
    architecture.thresholds = architecture_thresholds
    
    architecture.loop()
    print(architecture.reward)

In [120]:
if __name__ == "__main__":
    main()

============1 epochs============
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize cup=======
4. ======activate : recognize bottle=======
5. ======activate : pick up bottle=======
6. ======activate : put bottle down=======
7. ======activate : recognize cup=======
8. ======activate : recognize bottle=======
9. ======activate : recognize cup=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize bottle=======
3. ======activate : recognize cup=======
4. ======activate : pick up cup=======
5. ======activate : recognize bottle=======
6. ======activate : pick up bottle=======
7. ======activate : put cup down=======
8. ======activate : recognize cup=======
9. ======activate : recognize bottle=======
10. ======activate : pick up cup=======
11. ======activate :

6. ======activate : recognize bottle=======
7. ======activate : pick up cup=======
8. ======activate : recognize bottle=======
9. ======activate : recognize cup=======
10. ======activate : recognize bottle=======
11. ======activate : pick up bottle=======
12. ======activate : put bottle down=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize bottle=======
4. ======activate : pick up bottle=======
5. ======activate : recognize cup=======
6. ======activate : recognize bottle=======
7. ======activate : put cup down=======
8. ======activate : pick up cup=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize cup=======
3. ======activate : pick up bottle=======
4. ======activate : recognize bottle=======
5. ======activate : pick up cup=======
6. =====

6. ======activate : pick up bottle=======
7. ======activate : put cup down=======
8. ======activate : pick up cup=======
9. ======activate : recognize bottle=======
10. ======activate : poor liquid=======
11. ======activate : bring mouth to cup=======
12. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize cup=======
3. ======activate : pick up cup=======
4. ======activate : pick up bottle=======
5. ======activate : recognize bottle=======
6. ======activate : recognize cup=======
7. ======activate : recognize bottle=======
8. ======activate : put cup down=======
9. ======activate : pick up cup=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize cup=======
3. ======activate : pick up cup=======
4. ======activate : recognize cup=======
5. ======activate : recogn

11. ======activate : put bottle down=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize bottle=======
4. ======activate : pick up bottle=======
5. ======activate : put bottle down=======
6. ======activate : recognize cup=======
7. ======activate : recognize bottle=======
8. ======activate : pick up bottle=======
9. ======activate : put bottle down=======
10. ======activate : recognize cup=======
11. ======activate : recognize bottle=======
12. ======activate : recognize cup=======
13. ======activate : recognize bottle=======
14. ======activate : pick up bottle=======
15. ======activate : recognize bottle=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize bottle=======
4. ======activate : pick up bottle=====

7. ======activate : recognize bottle=======
8. ======activate : recognize cup=======
9. ======activate : pick up cup=======
10. ======activate : pick up bottle=======
11. ======activate : poor liquid=======
12. ======activate : bring cup to mouth=======
13. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : put cup down=======
4. ======activate : recognize bottle=======
5. ======activate : pick up bottle=======
6. ======activate : pick up cup=======
7. ======activate : recognize cup=======
8. ======activate : recognize bottle=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize bottle=======
4. ======activate : pick up bottle=======
5. ======activate : poor liquid=======
6. ======activate : bring

...

1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : bring mouth to cup=======
6. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize bottle=======
3. ======activate : recognize bottle=======
4. ======activate : recognize cup=======
5. ======activate : pick up cup=======
6. ======activate : put cup down=======
7. ======activate : pick up cup=======
8. ======activate : recognize bottle=======
9. ======activate : recognize cup=======
10. ======activate : recognize bottle=======
11. ======activate : pick up bottle=======
12. ======activate : poor liquid=======
13. ======activate : bring cup to mouth=======
14. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate 

8. ======activate : bring mouth to cup=======
9. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize cup=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : bring mouth to cup=======
6. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : pick up cup=======
5. ======activate : poor liquid=======
6. ======activate : bring cup to mouth=======
7. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize bottle=======
2. ======activate : recognize cup=======
3. ======activate : pick up cup=======
4. ======activate : pick up bottle======

1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : bring mouth to cup=======
6. ======activate : pick up cup=======
7. ======activate : put cup down=======
8. ======activate : recognize cup=======
9. ======activate : bring mouth to cup=======
10. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : pick up cup=======
5. ======activate : put cup down=======
6. ======activate : poor liquid=======
7. ======activate : recognize cup=======
8. ======activate : recognize cup=======
9. ======activate : recognize bottle=======
10. ======activate : recognize cup=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : rec

3. ======activate : recognize cup=======
4. ======activate : poor liquid=======
5. ======activate : pick up cup=======
6. ======activate : put cup down=======
7. ======activate : bring mouth to cup=======
8. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : pick up cup=======
6. ======activate : bring cup to mouth=======
7. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : bring mouth to cup=======
6. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ==

5. ======activate : recognize cup=======
6. ======activate : pick up cup=======
7. ======activate : put cup down=======
8. ======activate : poor liquid=======
9. ======activate : bring mouth to cup=======
10. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : recognize bottle=======
3. ======activate : pick up bottle=======
4. ======activate : poor liquid=======
5. ======activate : pick up cup=======
6. ======activate : put cup down=======
7. ======activate : bring mouth to cup=======
8. ======activate : drink=======
['be polite', 'object observed', 'hand empty1', 'hand empty2', 'cup empty']
1. ======activate : recognize cup=======
2. ======activate : pick up cup=======
3. ======activate : recognize bottle=======
4. ======activate : pick up bottle=======
5. ======activate : poor liquid=======
6. ======activate : bring mouth to cup=======
7. ======activate : bring cup to m